# SNOW ASSETS WRAPPER
#### Author: Luis A. Urso
#### Date: 04-Aug-2023
#### Version 2.0

### Dev To Do


1 - Create a JSON file for Location to allow relationship with Assets - DONE (testing and improving - maybe include a specific field with explicid location sys_id) <p>
2 - Implement Log Points either for Key Execution points + Errors <p>
3 - Implement HTTP Errors Handling - DOING (implemented for Locations)
4 - Implement Error Handling - Process Timing Control <=60 secs per API Request
5 - Run the routine for Computers and Mobile Devices (analise the model_categories available)

### Error Handling Messages



00 - Asset Wrapper Started<p>
99 - Asset Wrapper Finished<p>
01 - LOCATIONS RETRIEVE - REST API Error 401 after 3 tentatives to process<p>

### Required Packages

In [3]:
## Load required packages

import requests
import json
import time
from time import gmtime, strftime

### Global Variables & Setup

In [4]:
proc_tries=3 # Amount of times to retry REST API request in case of error

### Log Function

In [6]:
## Log Function Definition 
## The file will be generated in CSV using a Semi-Colon to separete the DateTime
## and Message. This is to allow usage of Comma

## Open the Log File for Append

logfile = open("asset_wrapper_log.csv","a")

## Message Log
def log_registry(log_message):
    dt_now=strftime("%a, %d %b %Y %H:%M:%S", gmtime())
    dt_now=dt_now + " - GMT"
    
    log_text=dt_now + ";" + log_message + "\n"
    
    logfile.write(log_text) # Created the JSON Opening Tag
    

### API Connecton Setup

In [10]:
## Set the API Authorizatoin and Return Type

## Set the Authorization

user = 'REST_GISSReport_Standard'

pwd = input('Type the Password?')

## Set proper header to work with JSON files 
headers = {"Accept":"application/json"}

### LOCATIONS - Get Locations SYS_IDS based on the Country Codes

In [13]:
## Log the Begin of the Execution

log_registry("00 - Asset Wrapper Started")

## Get the SNOW LOCATIONS by Country Code

ls_countries=['BRA'] # Add the Countries Code to Extract the data
## ls_countries=['ARG','BRA','COL','CRI','ECU','MEX','PER'] 
ls_loc_sys_id=[]
loc_sys_id=""

## Initialize the locations_wrapper.json file 
json_tag_open='{"result": ['
json_tag_close="]}"
outputf = open("locations_wapper.json","w")
outputf.write(json_tag_open) # Created the JSON Opening Tag

## Iterates amongst the countries to get the locations

for country in ls_countries:
    
    proc_count=1
    proc_error=True
    
    query='https://lilly.service-now.com/api/now/table/cmn_location?sysparm_display_value=true&sysparm_exclude_reference_link=true&sysparm_limit=10000&country='+country
    
    
    while (proc_count <= proc_tries) and (proc_error==True):
        
        ## Run the SNOW API Query
        start_time=time.time()
        response_loc = requests.get(query, auth=(user, pwd), headers=headers)
        end_time=time.time()
        print(response_loc.status_code)
        if response_loc.status_code==200:
            proc_error=False
        else:
            proc_count+=1
                
    if proc_count>proc_tries:
        proc_error=True
        proc_time=end_time-start_time
        proc_time_txt=str(proc_time)
        log_registry("01 - LOCATIONS RETRIEVE for Country Code "+country+" - REST API Error "+str(response_loc.status_code)+" after "+str(proc_count-1)+" tentatives to process. REST API average execution time "+proc_time_txt)
            
    
    
    if proc_error==False:   
        
        ## Transform response to JSON
              
        response_loc_dic = response_loc.json()
        
        ## Dumps the JSON content to file
        
        outputs = json.dumps(response_loc_dic["result"])
        print("Response:",outputs)
                
        if outputs!="[]":
            
            print("Writting:",loc_sys_id)
            print("Output Size:",len(outputs))
            
            outputf.write(outputs[1:len(outputs)-1])
            outputf.write(',')
        else:
            print("Ingored:",loc_sys_id)
                
        ##
        ## Creates a list to load the locations to be used to retrieve the assets
        ##
        
        idx=0
        
        try:
            while True:
                
                loc_sys_id = response_loc_dic["result"][idx]["sys_id"]
                ls_loc_sys_id.append(loc_sys_id) 
                idx+=1
                
        except IndexError:
            
            print("<END-OF-LOCATION>")

## Close the JSON Output file
outputf.write(json_tag_close) # Create the JSON Closing Tag
outputf.close() 

print("Found:",len(ls_loc_sys_id),"locations")


401
401
401
Found: 0 locations


In [ ]:
## Dev Convept only to solve the JSON output file generation due lack of RECORD in some entries. 

idx=0
error = True

while error==True: 
   try:
       print(response_loc_dic["result"][idx]["sys_id"],response_loc_dic["result"][idx]["u_facility_description"])
       idx+=1
   except:
       error=False
       print("Parou")

In [10]:
## How to make the Replace of JSON key.

for item in response_loc_dic["result"]:
    item["country"]=item["country"].replace("BRA","TESTE")
    
print(response_loc_dic)

{'result': [{'latitude_old': '', 'country': 'TESTE BR Federative Republic of Brazil', 'parent': '', 'cmn_location_type': None, 'u_country_code': 'BR Federative Republic of Brazil', 'city': 'Sao Paulo', 'longitude_old': '', 'u_location_type': 'Data Center', 'latitude': '', 'primary_location': '', 'managed_by_group': '', 'sys_updated_on': '2017-05-26 09:22:58', 'u_external_key': '', 'sys_id': '22f57cdb0f7f310028ed6509b1050e07', 'sys_updated_by': 'JL34778', 'life_cycle_stage_status': '', 'stock_room': 'false', 'street': 'Morumbi Av. 8264, ZipCode 04703-002, Brooklin, São Paulo, Brazil', 'sys_created_on': '2015-05-08 09:29:36', 'contact': '', 'phone_territory': '', 'u_facilities_code': '', 'u_active': 'true', 'company': '', 'lat_long_error': '', 'state': 'BR', 'sys_created_by': 'JL34778', 'longitude': '', 'zip': '04703-002', 'u_country_description': '', 'u_building_code': '', 'sys_mod_count': '2', 'duplicate': 'false', 'sys_tags': '', 'time_zone': None, 'u_zone': 'ZONE1', 'cmn_location_sou

### ASSETS - Get the Asset Records for All Locations SYS_IDS for the Country Codes 

In [25]:
## Model Categories to Retriece

ls_model_category = ['Computer','Handheld Device']

## Get the Assets for each Locations related to the provided Country Codes

loc_count=0

## Create/Open JSON Output file

json_tag_open='{"result": ['
json_tag_close="]}"

outputf = open("assets_wapper.json","w")

outputf.write(json_tag_open) # Created the JSON Opening Tag

## Iterates over all location to extract the asset data

for model_category in ls_model_category:

    for loc_sys_id in ls_loc_sys_id:

        query='https://lilly.service-now.com/api/now/table/alm_asset?sysparm_display_value=true&sysparm_exclude_reference_link=false&sysparm_limit=10000&model_category='+model_category+'&location='+loc_sys_id
        response_asset = requests.get(query, auth=(user, pwd), headers=headers)

        loc_count+=1
        print("Processing Location ",loc_count,'of',len(ls_loc_sys_id),"-",loc_sys_id)
        
        
        response_asset_dic=response_asset.json()

        ##
        ## Dumps the JSON content to file
        ##
        
        outputs = json.dumps(response_asset_dic["result"])
        print("Response:",outputs)
        if outputs!="[]":
            
            print("Writting:",loc_sys_id)
            print("Output Size:",len(outputs))
            
            outputf.write(outputs[1:len(outputs)-1])
            outputf.write(',')
        else:
            print("Ingored:",loc_sys_id)

## Close ther JSON Output file
outputf.write(json_tag_close) # Create the JSON Closing Tag
outputf.close()
    

Processing Location  1 of 16 - 22f57cdb0f7f310028ed6509b1050e07
Response: []
Ingored: 22f57cdb0f7f310028ed6509b1050e07
Processing Location  2 of 16 - 2596a27b1968c1001f5d98e0f5921994
Response: [{"u_altiris": "false", "parent": "", "skip_sync": "false", "u_dwac_asset_tag": "", "cmn_lease_expiration_date": "", "cmn_lease_contract": "", "residual_date": "", "residual": "$0.00", "sys_updated_on": "2023-04-24 12:44:08", "request_line": "", "resold_value": "$0.00", "sys_updated_by": "C297703", "due_in": null, "cmn_monthly_lease_payment": "$0.00", "model_category": {"display_value": "Computer", "link": "https://lilly.service-now.com/api/now/table/cmdb_model_category/81feb9c137101000deeabfc8bcbe5dc4"}, "sys_created_on": "2021-07-30 23:33:50", "sys_domain": {"display_value": "global", "link": "https://lilly.service-now.com/api/now/table/sys_user_group/global"}, "disposal_reason": "", "sn_itam_common_last_audit_state": null, "model": {"display_value": "DELL LATITUDE 7390", "link": "https://lilly

### Finalization Routing / Garbage Collection

In [24]:

## Log the Begin of the Execution

log_registry("99 - Asset Wrapper Finished")

## Closes the logfile 

logfile.close()